#🧬 Pneuma Encoder con Frecuencias EEG
Reconstrucción neuronal adaptativa.


In [ ]:
# Optimizer selector (AdamW / Lion)
import torch
from lion_pytorch import Lion

def get_optimizer(model, optimizer_name='adamw', lr=1e-4, weight_decay=1e-2):
    if optimizer_name.lower() == 'adamw':
        return torch.optim.AdamW(model.parameters(), lr=lr, weight_decay=weight_decay)
    elif optimizer_name.lower() == 'lion':
        return Lion(model.parameters(), lr=lr, weight_decay=weight_decay)
    else:
        raise ValueError(f"Unsupported optimizer: {optimizer_name}")

ModuleNotFoundError: No module named 'lion_pytorch'

In [ ]:
!pip install lion_pytorch

In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.neighbors import NearestNeighbors
from tensorflow.keras.models import Model
from tensorflow.keras.layers import Input, Dense
from tensorflow.keras.optimizers import Adam

## 🔄 Fractalización Frecuencial

In [ ]:
def fractalizar_frecuencia(vector):
    return np.clip(np.sin(np.pi * vector * 3) + vector * 0.5, 0, 1)

## 📊 Dataset de Frecuencias Cerebrales

In [ ]:
data = {
 'Región': ['Frontal','Parietal','Temporal','Occipital','Central'],
 'Delta_Sano':[0.25,0.20,0.18,0.15,0.22],
 'Theta_Sano':[0.30,0.28,0.25,0.23,0.29],
 'Alpha_Sano':[0.70,0.65,0.68,0.60,0.72],
 'Beta_Sano':[0.55,0.52,0.50,0.48,0.54],
 'Gamma_Sano':[0.60,0.62,0.61,0.58,0.63],
 'Delta_AD':[0.55,0.53,0.52,0.50,0.58],
 'Theta_AD':[0.45,0.42,0.40,0.38,0.44],
 'Alpha_AD':[0.42,0.39,0.41,0.36,0.43],
 'Beta_AD':[0.40,0.39,0.37,0.41,0.43],
 'Gamma_AD':[0.52,0.50,0.48,0.46,0.51]
}
df = pd.DataFrame(data)
df

Región  Delta_Sano  Theta_Sano  Alpha_Sano  Beta_Sano  Gamma_Sano  \
0    Frontal        0.25        0.30        0.70       0.55        0.60   
1   Parietal        0.20        0.28        0.65       0.52        0.62   
2   Temporal        0.18        0.25        0.68       0.50        0.61   
3  Occipital        0.15        0.23        0.60       0.48        0.58   
4    Central        0.22        0.29        0.72       0.54        0.63   

   Delta_AD  Theta_AD  Alpha_AD  Beta_AD  Gamma_AD  
0      0.55      0.45      0.42     0.40      0.52  
1      0.53      0.42      0.39     0.39      0.50  
2      0.52      0.40      0.41     0.37      0.48  
3      0.50      0.38      0.36     0.41      0.46  
4      0.58      0.44      0.43     0.43      0.51

## ⚙️ Entrenamiento Autoencoder (Adam/RAdam)

In [ ]:
X_sano, X_ad = df.iloc[:,1:6].values, df.iloc[:,6:].values
input_dim = X_sano.shape[1]

input_layer = Input(shape=(input_dim,))
encoded = Dense(3, activation='relu')(input_layer)
decoded = Dense(input_dim, activation='sigmoid')(encoded)

autoencoder = Model(input_layer, decoded)
autoencoder.compile(optimizer=Adam(0.01), loss='mse')

# Epochs masivos (ajustables)
history = autoencoder.fit(X_sano, X_sano, epochs=200000, verbose=0)
history_fine = autoencoder.fit(X_sano, X_sano, epochs=300000, verbose=0)

## 📉 Visualización explícita de pérdida (Loss)

In [ ]:
plt.figure(figsize=(10,5))
plt.plot(history.history['loss'] + history_fine.history['loss'], label='Pérdida (Loss)')
plt.title('Pérdida del Entrenamiento del Autoencoder')
plt.xlabel('Época'); plt.ylabel('Loss'); plt.legend()
plt.show()

## 🧪 Reconstrucción con Levofrecuencia Adaptativa

In [ ]:
def levofrecuencia_adaptativa(vec, ae, orig, e=25, d=0.05, lr=0.1):
    best, best_cos, mod, delta = vec, 0, vec.copy(), d
    for _ in range(e):
        mod = np.clip(mod + np.random.uniform(-delta,delta,vec.shape) + 0.1*np.sin(2*np.pi*mod),0,1)
        rec = ae.predict(mod.reshape(1,-1), verbose=0)
        cos = cosine_similarity(orig.reshape(1,-1), rec)[0][0]
        if cos>best_cos: best_cos, best = cos, mod
        delta*=(1-cos)*lr
    return best

## 🔍 Localización Explícita de Redes Alternas (Memoria Inaccesible)

In [ ]:
neighbors = NearestNeighbors(n_neighbors=1).fit(X_rewards)
aprendizaje,conciencia=[],[]
for i,original in enumerate(X_ad):
    rec=rewards.predict(lo_aprendido.reshape(1,-1),verbose=0)
    cos=cosine_similarity(lo_aprendido.reshape(1,-1),rec)[0][0]
    if cos<0.98:
        rec_mod=levolearning_adaptative(rec[0],rewards,lo_aprendido)
        rec_mod=rewards.predict(rec_mod.reshape(1,-1),verbose=0)
        cos=cosine_similarity(lo_aprendido.reshape(1,-1),rec_mod)[0][0]
    aprendizaje.append(rec)
    aprendizaje_conciente.append(cos)
aprendizaje_consciente=np.array(conciencia)

## 📊 Análisis de pérdidas post-entrenamiento

In [ ]:
full_loss = history.history['loss'] + history_fine.history['loss']
min_loss, min_epoch = min(full_loss), full_loss.index(min(full_loss))
final_loss = full_loss[-1]
total_epochs = len(full_loss)

print(f"🔎 Pérdida mínima: {min_loss:.6f} en época {min_epoch}")
print(f"🔎 Pérdida final: {final_loss:.6f}")
print(f"🔎 Total de épocas: {total_epochs}")

## 💾 Guardado del modelo

In [ ]:
autoencoder.save("NeuroCIES_Encoder_Optimo.h5")
print("✅ Modelo guardado como: NeuroCIES_Encoder_Optimo.h5")

## 📈 Similitud Coseno y Reportes finales

In [ ]:
X_reconstruido = autoencoder.predict(X_sano)
similitudes = [cosine_similarity(X_sano[i].reshape(1,-1), X_reconstruido[i].reshape(1,-1))[0][0]
               for i in range(len(X_sano))]
print(f"🌐 Similitud promedio global: {np.mean(similitudes):.6f}")
print(f"🌐 Máxima similitud: {np.max(similitudes):.6f}")
print(f"🌐 Mínima similitud: {np.min(similitudes):.6f}")